## 1. 준비단계: train_test_split 주요 매개변수
- test_size: 테스트 세트의 비율을 지정합니다.
- 25% 테스트에 사용하고, 75% 테스트로 사용하기 위해서 나눠주는 예시 코드
  * X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=2022)
<br>
<br>
- random_state: 난수 생성기의 시드를 설정하여 데이터 분할을 재현 가능하게 합니다.
  * random_state 값을 사용하면, 같은 데이터를 여러 번 나누더라도 항상 동일한 방식으로 훈련 세트와 테스트 세트가 생성
  * 동일한 시드 값으로 초기화된 난수 생성기는 항상 동일한 난수 시퀀스를 생성합니다. 
  * 위의 예시에서 42, 1234, 2022 등 어떤 숫자도 시드 값으로 사용할 수 있습니다. 중요한 것은 동일한 시드 값을 사용하면 항상 같은 결과를 얻을 수 있다는 점

In [1]:
# pandas 라이브러리를 임포트
# pandas는 데이터 조작과 분석을 위한 강력한 라이브러리로,
# 특히 데이터프레임(dataframe) 구조를 사용하여 데이터 처리를 용이하게 함
import pandas as pd

# scikit-learn의 model_selection 모듈에서 train_test_split 함수를 임포트
# scikit-learn은 기계 학습을 위한 라이브러리로, 다양한 모델과 도구를 제공함
# train_test_split 함수는 데이터를 훈련 세트와 테스트 세트로 나누는 데 사용됨
from sklearn.model_selection import train_test_split

# "bands.csv" 파일을 읽어와서 데이터프레임으로 변환
df = pd.read_csv("bands.csv")

# 데이터프레임에서 종속 변수 'y' 열을 제외한 모든 열을 독립 변수 X로 정의
# axis=1 >> 열을 기준으로 삭제한다는 뜻
# drop('y', axis=1): 'y' 열을 삭제하라는 명령입니다
# X: 'y' 열이 제거된 새로운 데이터프레임으로, 독립 변수들만을 포함
X = df.drop('y', axis=1)


# 데이터프레임에서 종속 변수 'y' 열만을 종속 변수 y로 정의
y = df['y']

# 데이터를 훈련 세트와 테스트 세트로 분할
# train_test_split 함수는 X와 y를 입력으로 받아, 이를 훈련 세트와 테스트 세트로 나눕니다. 반환값은 네 개의 배열로 구성
# X는 독립 변수, y는 종속 변수
# random_state=2022는 난수 생성기의 시드를 설정하여 결과의 재현성을 보장
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=2022)


## 2. 파이프라인에 들어갈 임퓨터, 스케일러, 분류모델 인스턴스 정의
### 아래 코드에서 임퓨터, 스케일러, 모델 모두 학습하지 않았음! !
**1. 임퓨터 (Imputer)**<br>
- 임퓨터는 데이터에서 결측값을 처리하는 방법을 제공합니다. 결측값이 있는 데이터셋을 그대로 사용할 경우, 많은 머신러닝 알고리즘이 제대로 작동하지 않거나 성능이 저하될 수 있습니다. 따라서, 결측값을 적절히 대체하는 것이 중요합니다.
- SimpleImputer: 가장 많이 사용되는 임퓨터 중 하나로, 결측값을 특정 값(평균, 중앙값, 최빈값 등)으로 대체합니다.

**2. 스케일러 (Scaler)**<br>
- 스케일러는 데이터를 표준화(standardization) 또는 정규화(normalization)하는 도구
- 특히, 거리 기반 알고리즘(K-NN, SVM 등)이나 경사 하강법을 사용하는 알고리즘에서는 데이터의 스케일이 매우 중요
    * MinMaxScaler: 데이터를 0과 1 사이의 범위로 변환합니다.
    * tandardScalerler: 데이터를 평균이 0, 분산이 1이 되도록 표준화합니다.

In [2]:
from sklearn.impute import SimpleImputer  # 결측값을 대체하기 위한 SimpleImputer 클래스 임포트
from sklearn.preprocessing import MinMaxScaler  # 데이터 정규화를 위한 MinMaxScaler 클래스 임포트
from sklearn.svm import SVC  # 서포트 벡터 머신(SVM) 분류 모델을 위한 SVC 클래스 임포트

# 결측값을 평균값으로 대체하는 SimpleImputer 인스턴스 생성
# strategy="mean"은 결측값을 해당 열의 평균값으로 대체하도록 지정
imputer = SimpleImputer(strategy="mean")

# 데이터를 0과 1 사이의 범위로 정규화하는 MinMaxScaler 인스턴스 생성
scaler = MinMaxScaler()

# RBF 커널을 사용하는 서포트 벡터 머신(SVM) 분류 모델 인스턴스 생성
# kernel="rbf"는 방사형 기저 함수(RBF) 커널을 사용하여 데이터를 비선형적으로 분류
model = SVC(kernel="rbf")


## 3. 파이프라인 생성 및 학습
* 각 단계는 순차적으로 실행되며, 결측값 대체 -> 데이터 정규화 -> 모델 학습의 순서로 진행됩니다.

In [4]:
from sklearn.pipeline import Pipeline  # Pipeline 클래스를 임포트

# 파이프라인 구성 요소를 지정하여 파이프라인 객체를 생성
# 첫 번째 단계는 결측값을 대체하는 imputer, 두 번째 단계는 데이터를 정규화하는 scaler, 세 번째 단계는 분류 모델인 SVM
P = Pipeline([("imputer", imputer), ("scaler", scaler), ("model", model)])

# 훈련 데이터를 사용하여 파이프라인을 학습
P.fit(X_train, y_train)

# # 개별 단계로 수행했을 때와 동일한 작업
# X_imputed = imputer.fit_transform(X_train)  # 결측값 대체
# X_scaled = scaler.fit_transform(X_imputed)  # 데이터 정규화
# model.fit(X_scaled, y_train)  # 모델 학습


Pipeline(steps=[('imputer', SimpleImputer()), ('scaler', MinMaxScaler()),
                ('model', SVC())])

In [5]:
display(P.predict(X_test))

array([0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1,
       1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1,
       1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1,
       1, 0, 1, 0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1,
       1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1,
       1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 1,
       1, 1, 1], dtype=int64)